# TD 4 : Code cycliques, suite : codes BCH


Les codes BCH (Bose-Chaudhuri-Hocquenghem) ont été inventés en 1959 par le mathématicien français Alexis Hocquenghem et indépendamment en 1960 par Raj Chandra Bose et D. K. Ray-Chaudhuri. Ce sont des codes cycliques utilisant les propriétés des corps finis $\mathbb F_{p^m}$. Ils se construisent à partir d'un polynôme générateur $g$, défini comme le plus petit commun multiple de polynômes minimaux associés aux puissances d'une racine primitive du corps fini. Cette construction donne un code de longueur $n = p^m -1$ et garantit une distance minimale choisie à l'avance $d$, permettant de corriger jusqu'à $t = \lfloor \frac{d-1}{2} \rfloor$ erreurs. La dimension du code nécessite un calcul pour être connue exactement.



Le caractère cyclique des codes BCH permet une implémentation efficace des opérations d'encodage et de décodage, tout en offrant un contrôle précis sur la capacité de correction. Par exemple, pour $m=4$ et $t=2$, on obtient un code $[15,7,5]$ capable de corriger jusqu'à deux erreurs dans un mot de code de $15$ bits.

Les codes BCH sont utilisés dans des applications telles que les communications par satellite, les lecteurs de CD, les DVD, les disques durs, les clés USB, les disques SSD et les codes-barres bidimensionnels.


# 1. Considérations algébriques

Soit $p$ un nombre premier, $m$ un entier et $d>0$ une distance fixée. On peut définir le corps fini $\mathbb F_{p^m}$ comme le corps de décomposition du polynôme $X^{p^m} - X$. 
On peut montrer (on ne le fera pas) que le groupe des inversibles $\mathbb F_{p^m}^{\times}$ est *cyclique* donc engendré par un élément que l'on notera $\alpha$ dans la suite. On appelle un tel $\alpha$ un *élément primitif* de $\mathbb F_{p^m}$. 

On définit $m_i(X)$ comme le polynôme minimal de $\alpha^i$ dans $\mathbb{F}_p$ et $L = PPCM(m_1,...,m_{d-1})$. 

1.1 Rappeler pourquoi $m_i(X)$ existe. Montrer que $L$ divise $X^n - 1$. 

1.2 Montrer que $deg L \leq (d-1)m $. Par le cours, en déduire une borne inférieure sur la longueur du message à coder (i.e. sur le $k$ dans $[n,k,d]$). Commenter : est il proche d'être MDS ? Parfait (prendre $d = 1$ ou $2$) ?

1.3 On va montrer que le code $BCH$ engendré par $L$ est bien de distance $d$. On rappelle que le code cyclique engendré par le polynôme $L$ est l'idéal $(L)$ engendré par $L$ dans $\mathbb F_p[X]/(X^n-1)$. On procède par l'absurde. Soit $p(x) \in (L)$ de poids strictement inférieur à $d$. On peut donc noter
    $$p(x) = b_1 x^{k_1} + \dots + b_{d-1} x^{k_{d-1}}$$
    avec $k_1 < \cdots < k_{d-1}$. 

a) Expliquer pourquoi $p$ annule les $\alpha, \alpha^2, ... \alpha^{d-1}$. En déduire que
 $$\begin{bmatrix}
          1 &      1 & \cdots &       1 \\
      \alpha^{k_1} &   \alpha^{k_2} & \cdots &   \alpha^{k_{d-1}} \\
                 \vdots &              \vdots &        &                  \vdots \\
    \alpha^{(d-2)k_1} & \alpha^{(d-2)k_2} & \cdots & \alpha^{(d-2)k_{d-1}} \\
  \end{bmatrix} \begin{bmatrix}
    b_1 \\ b_2 \\ \vdots \\ b_{d-1}
  \end{bmatrix} = \begin{bmatrix}
    0 \\ 0 \\ \vdots \\ 0
  \end{bmatrix}.$$

b) Conclure.

# 2. Implémentation du code BCH

On utilisera le module ``galois`` pour gérer les corps finis. S'il n'est pas installé, exécutez :

In [146]:
pip install galois

Note: you may need to restart the kernel to use updated packages.


(si ça ne marche pas, essayez conda install galois.)

On peut manipuler le corps fini $\mathbb F_{p^m}$ avec le module galois : 

In [147]:
import galois
F = galois.GF(2**4) #corps F_16
#Dans le module galois, les éléments d'un corps fini F de cardinal q sont numérotés de 0 à q-1. Mais attention ce ne sont que des choix de symboles. On n'est pas dans Z/qZ par exemple.
#Par exemple on peut prendre :
a=F(2); a, a**4

(GF(2, order=2^4), GF(3, order=2^4))

1). Ecrire une fonction ``ordre(a)`` qui prend un élément non nul d'un corps $F$ et calcule son ordre dans le groupe multiplicatif $F^\times$. Vérifiez avec cette fonction que ``a = F(2)`` est un générateur de $\mathbb{F}_{16}^\times$.

In [54]:
def ordre(a):
    pass

Le module galois possède des fonctions qui calculent des polynômes minimaux et leur ppcm :  

In [138]:
P=galois.FieldArray.minimal_poly(a)
Q=galois.FieldArray.minimal_poly(a**3)
print(P)
print(Q)
R = galois.lcm(P,Q) #calcule le PPCM de P et Q. 
R.coeffs#renvoyer les coefficients de R
H = galois.Poly([1,0,0,-1])
print(Q % H) #on peut prendre des modulo de polynômes facilement

x^4 + x + 1
x^4 + x^3 + x^2 + x + 1
x^2


2) En utilisant ces fonctions, calculer le polynôme $L$ du code BCH associé à $\alpha =$ ``F(2)``.

In [113]:
L=None

On va implémenter le code BCH pour un nombre premier $p$, des entiers $m$ et $d$ quelconques. Il faut pour ceci trouver un *élément primitif* du corps $\mathbb F_{p^m}$ : le module galois s'en charge.

In [144]:
K=galois.GF(3,5) #K = F_(3^5) = F_243
alpha=K.primitive_element; alpha #on obtient un élément primitif du corps K

GF(3, order=3^5)

En utilisant cette fonction et les précédentes, construire une fonction ``polynome_generateur(p,m,d)`` qui renvoie le polynôme générateur du code BCH associé à l'élément primitif $\alpha$. 

In [121]:
def polynome_generateur(p,m,d):

GF([1, 1, 1, 0, 1, 0, 0, 0, 1], order=2)

En déduire une fonction ``BCH_code(message, p,m,d)`` qui prend en entrée un message (sous forme de liste d'éléments de $\mathbb F_p$) et qui renvoie le code $BCH$ correpondant sous forme de liste d'éléments de $\mathbb F_p$ (je serai tolérant sur le type des objets que vous renvoyez ; tant que c'est lisible).  N'oubliez pas de tout calculer modulo $X^n -1$ (ce sont des codes cycliques !) et de vérifier que la longueur du message est compatible avec la longueur attendue en entrée.

Essayez d'encoder le message [0,1,0,0,1,1,1] sur $\mathbb F_2$ avec le code BCH $[15,7,5]$.

In [140]:
def BCH_code(message,p,m,d): pass